###  **Question 3: IAQF Academic Competition**


*Imports*

In [44]:
import pandas as pd 
import numpy as np
import yfinance as yf
from datetime import date
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression

##### **a) What are the implications of the noted concentration for that strategy?**

**Data**

*Reading*

In [45]:
sector_etfs = {
    'Baseline': {
        "Large-Cap": "SPY",
        "Small-Cap": "^SP600"
    },
    "Technology": {
        "Large-Cap": "XLK",
        "Small-Cap": "PSCT"
    },
    "Healthcare": {
        "Large-Cap": "XLV",
        "Small-Cap": "PSCH"
    },
    "Financials": {
        "Large-Cap": "XLF",
        "Small-Cap": "PSCF"
    },
    "Consumer Discretionary": {
        "Large-Cap": "XLY",
        "Small-Cap": "PSCD"
    },
    "Consumer Staples": {
        "Large-Cap": "XLP",
        "Small-Cap": "PSCC"
    },
    "Industrials": {
        "Large-Cap": "XLI",
        "Small-Cap": "PSCI"
    },
    "Energy": {
        "Large-Cap": "XLE",
        "Small-Cap": "PSCE"
    },
    "Materials": {
        "Large-Cap": "XLB",
        "Small-Cap": "PSCM"
    },
    "Utilities": {
        "Large-Cap": "XLU",
        "Small-Cap": "PSCU"
    },
    "Real Estate": {
        "Large-Cap": "XLRE",
        "Small-Cap": "ROOF"
    }
}

In [46]:
tickers = [_ for x in sector_etfs.values() for _ in x.values()]
start_date = date(2010,1,1)
end_date = date(2025,1,1)

# ETF Returns
prices = yf.download(tickers = tickers,start = start_date,end = end_date)['Close']

ff_data = pd.read_csv('../extra-data/FF_3Factor.CSV',skiprows = 4,index_col=0)
ff5_data = pd.read_csv('../extra-data/FF_5Factor.csv',index_col=0)

[*********************100%***********************]  22 of 22 completed


*Cleaning*

In [47]:
returns = prices.pct_change().dropna()

# Clean FF Data
ff_data = ff_data.iloc[:-1]
ff_data.index = pd.to_datetime(ff_data.index).date

ff5_data.index = pd.to_datetime(ff5_data.index).date

/var/folders/__/wgnmk9j14kl1krf80l2c6bfw0000gn/T/ipykernel_32991/1153697555.py:1: FutureWarning:

The default fill_method='pad' in DataFrame.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.



##### *i)* Baseline Strategy


Baseline strategy is underperforming, show how this is connected to tech exposure

In [48]:
baseline_strategy = pd.DataFrame(returns['^SP600'] - returns['SPY'],columns=['daily_returns'])
baseline_strategy['cumulative_returns'] = baseline_strategy['daily_returns'].cumsum()

##### *ii)* Industry Sector Basis

Show the strategy performance at a sector basis

In [49]:
sector_baseline_returns = {}

for sector,(large,small) in sector_etfs.items():
    sector_baseline_returns[sector] = (returns[sector_etfs[sector][small]] - returns[sector_etfs[sector][large]]).cumsum()

sector_baseline_returns = pd.DataFrame(sector_baseline_returns)

##### *iii)* Risk Attribution (Fama-French)

In [50]:
import statsmodels.api as sm
# Merge datasets
df = baseline_strategy.join(ff5_data, how='inner')

# Calculate excess returns
df['Excess_Return'] = df['daily_returns'] - df['rf']

# Run regression
X = df[['smb', 'hml', 'rmw', 'cma','umd']]
X = sm.add_constant(X)  # Add intercept
y = df['Excess_Return']

model = sm.OLS(y, X).fit()
print(model.summary())

# Extract risk contribution
betas = model.params[1:]  # Exclude intercept
factor_vols = df[['smb', 'hml', 'rmw', 'cma','umd']].std()  # Factor standard deviations

# Compute risk contribution
risk_contributions = (betas**2 * factor_vols**2) / sum(betas**2 * factor_vols**2)
print("Risk Attribution:\n", risk_contributions)

                            OLS Regression Results                            
Dep. Variable:          Excess_Return   R-squared:                       0.933
Model:                            OLS   Adj. R-squared:                  0.933
Method:                 Least Squares   F-statistic:                     2087.
Date:                Mon, 24 Feb 2025   Prob (F-statistic):               0.00
Time:                        10:44:32   Log-Likelihood:                 3557.5
No. Observations:                 753   AIC:                            -7103.
Df Residuals:                     747   BIC:                            -7075.
Df Model:                           5                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.0003   7.88e-05     -3.639      0.0

In [51]:
risk_contributions

smb    0.936012
hml    0.054043
rmw    0.008694
cma    0.001240
umd    0.000011
dtype: float64

#### **Plots**

*i)* Baseline Strategy Performance

In [52]:
returns['SPY']

Date
2015-10-09    0.000597
2015-10-12    0.000944
2015-10-13   -0.006302
2015-10-14   -0.004794
2015-10-15    0.015355
                ...   
2024-12-24    0.011115
2024-12-26    0.000067
2024-12-27   -0.010527
2024-12-30   -0.011412
2024-12-31   -0.003638
Name: SPY, Length: 2322, dtype: float64

In [53]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x = baseline_strategy.index,
        y = baseline_strategy['cumulative_returns'],
        name = 'Baseline Strategy',
        line=dict(color='black', width=4)
    )
)

fig.add_trace(
    go.Scatter(
        x = returns.index,
        y = returns['SPY'].cumsum(),
        name = 'S&P 500 Large Cap'
    )
)

fig.add_trace(
    go.Scatter(
        x = returns.index,
        y = returns['^SP600'].cumsum(),
        name = 'S&P 600 Small Cap'
    )
)

fig.update_layout(title = 'Benchmark Strategy Returns')
fig.update_layout(
                  showlegend=True,
                  margin=dict(l=10, r=10, t=50, b=10),
                  legend=dict(orientation="h",yanchor="top",y=-0.1,xanchor="center",x=0.5),
                  width = 800,height = 550,
                  xaxis_title = 'Date',
                  xaxis=dict(title_standoff=3) 
                )
fig.update_yaxes(title = 'Cumulative Simple Returns')
fig.update_xaxes(title = 'Date')
fig.show()

*ii)* Strategy at Sector Level

In [54]:
fig = go.Figure()


for strategy in sector_baseline_returns:

    fig.add_trace(
        go.Scatter(
            x = sector_baseline_returns.index,
            y = sector_baseline_returns[strategy],
            name = strategy
        )
    )

fig.update_layout(title = 'Strategy Sector Level Returns')
fig.update_layout(
                  showlegend=True,
                  margin=dict(l=10, r=10, t=50, b=10),
                  legend=dict(orientation="h",yanchor="top",y=-0.1,xanchor="center",x=0.5),
                  width = 800,height = 550,
                  xaxis_title = 'Date',
                  xaxis=dict(title_standoff=3) 
                )
fig.update_yaxes(title = 'Cumulative Simple Returns')
fig.update_xaxes(title = 'Date')
fig.show()

In [55]:
ff_data.index = pd.to_datetime(ff_data.index)

In [56]:
ff_data['Year'] = ff_data.index.year

In [57]:
ff_yearly = ff_data.groupby('Year').agg({"SMB":'sum'}).reset_index()

In [58]:
ff_yearly = ff_yearly[ff_yearly['Year'] >= 2018]

In [59]:
ff_yearly.to_latex()

'\\begin{tabular}{lrr}\n\\toprule\n & Year & SMB \\\\\n\\midrule\n92 & 2018 & -3.080000 \\\\\n93 & 2019 & -4.570000 \\\\\n94 & 2020 & 12.020000 \\\\\n95 & 2021 & -2.390000 \\\\\n96 & 2022 & -6.290000 \\\\\n97 & 2023 & -1.250000 \\\\\n98 & 2024 & -8.190000 \\\\\n\\bottomrule\n\\end{tabular}\n'

In [60]:

fig = go.Figure()


fig.add_trace(
    go.Scatter(
        x = ff_yearly['Year'],
        y = ff_yearly['SMB']
    )
)

fig.show()

##### **b) How would you modify the trading strategy to correct for any implication you may have found?**

In [61]:
small_cap = ['PSCT', 'PSCH', 'PSCF','PSCD', 'PSCC', 'PSCI', 'PSCE', 'PSCM','PSCU','ROOF']
large_cap = ['XLK', 'XLV', 'XLF', 'XLY', 'XLP', 'XLI', 'XLE', 'XLB', 'XLU', 'XLRE']

start_date = date(2020,1,1)
end_date = date(2025,1,1)

data = yf.download(tickers = small_cap + large_cap,start = start_date, end = end_date)['Close']

returns = data.pct_change().dropna()

[*********************100%***********************]  20 of 20 completed
/var/folders/__/wgnmk9j14kl1krf80l2c6bfw0000gn/T/ipykernel_32991/3941965587.py:9: FutureWarning:

The default fill_method='pad' in DataFrame.pct_change is deprecated and will be removed in a future version. Either fill in any non-leading NA values prior to calling pct_change or specify 'fill_method=None' to not fill NA values.



In [172]:
class Momentum:

    def __init__(self, data, returns, lookback, rebalance, type = 'Equal'):
        # Inputs
        self.data = data
        self.returns = returns
        self.lookback = lookback
        self.rebalance = rebalance
        self.type = type

        # Stats
        self.weights = pd.Series(0.0, index=self.returns.columns, dtype=float)
        self.portfolio_returns = pd.Series(0.0, index=self.returns.index, dtype=float)

    def run(self):

        for t in range(self.lookback, len(self.returns.index)):
            # Compute portfolio return for the day
            daily_return = (self.weights * self.returns.iloc[t]).sum()
            self.portfolio_returns.iloc[t] = daily_return

            if t % self.rebalance == 0:

                # Get window returns
                small_cap_window_returns = self.returns.iloc[t - self.lookback:t,][small_cap]
                large_cap_window_returns = self.returns.iloc[t - self.lookback:t,][large_cap]

                # Calculate momentum, long and short threshold
                momentum_small_cap = self.signal(small_cap_window_returns)
                momentum_large_cap = self.signal(large_cap_window_returns)

                # Select assets in the top and bottom deciles
                long_assets = momentum_small_cap.nlargest(6).index
                short_assets = momentum_large_cap.nsmallest(6).index

                # Equally Weighted Portfolio
                self.weights = pd.Series(0.0, index=self.returns.columns, dtype=float)
                self.weights[long_assets] = 1 / len(long_assets) if len(long_assets) > 0 else 0
                self.weights[short_assets] = -1 / len(short_assets) if len(short_assets) > 0 else 0

            

        # Clean + Compute Stats
        self._clean_returns()
        self._compute_stats()

    def signal(self, window_returns):
        """Calculate Momentum Signals"""
        if self.type == 'Equal':

            # Calculate momentum (cumulative returns over the lookback period)
            momentum = window_returns.prod() / window_returns.std()
    
            return momentum
        
    def _clean_returns(self):
        """Clean Portfolio Returns"""

        _df = pd.DataFrame(self.portfolio_returns,columns=['daily_return'])
        _df['cumulative_return'] = (1+ _df['daily_return']).cumprod()
        
        self.portfolio_returns = _df

    def _compute_stats(self):
        """Compute Portfolio Stats"""
        
        # Annualized Return
        annual_ret = self.portfolio_returns['daily_return'].mean()*252

        # Volatility
        annual_vol = self.portfolio_returns['daily_return'].std()*np.sqrt(252)

        # Sharpe Ratio
        sharpe_ratio = annual_ret / annual_vol

        self.stats = {'Sharpe Ratio': round(sharpe_ratio,2),
                      'Annual Return': round(annual_ret,2),
                        'Annual Volatility': round(annual_vol,2)}

In [173]:
m = Momentum(data,returns,30,30,'Equal')
m.run()
portfolio_returns = m.portfolio_returns

In [174]:
import statsmodels.api as sm
# Merge datasets
df = portfolio_returns.join(ff5_data, how='inner')

# Calculate excess returns
df['Excess_Return'] = df['daily_return'] - df['rf']

# Run regression
X = df[['smb', 'hml', 'rmw', 'cma','umd']]
X = sm.add_constant(X)  # Add intercept
y = df['Excess_Return']

model = sm.OLS(y, X).fit()
print(model.summary())

# Extract risk contribution
betas = model.params[1:]  # Exclude intercept
factor_vols = df[['smb', 'hml', 'rmw', 'cma','umd']].std()  # Factor standard deviations

# Compute risk contribution
risk_contributions = (betas**2 * factor_vols**2) / sum(betas**2 * factor_vols**2)
print("Risk Attribution:\n", risk_contributions)

                            OLS Regression Results                            
Dep. Variable:          Excess_Return   R-squared:                       0.659
Model:                            OLS   Adj. R-squared:                  0.656
Method:                 Least Squares   F-statistic:                     288.4
Date:                Mon, 24 Feb 2025   Prob (F-statistic):          1.16e-171
Time:                        12:22:29   Log-Likelihood:                 2926.0
No. Observations:                 753   AIC:                            -5840.
Df Residuals:                     747   BIC:                            -5812.
Df Model:                           5                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       -9.66e-05      0.000     -0.530      0.5

##### **c) Can you provide a backtest comparison between the standard strategy and the modified strategy?**

In [175]:
fig = go.Figure()


fig.add_trace(
    go.Scatter(
        x = portfolio_returns.index,
        y = portfolio_returns['cumulative_return'],
    )
)


fig.update_layout(title = 'v3')
fig.show()

### **Improvements 2**

**Data**

In [250]:
import pandas as pd

def get_sp_table(url):
    tables = pd.read_html(url)
    return tables[0]

def get_sp_tickers(url, column_name):
    """Fetch tickers from the given Wikipedia URL and extract the specified column."""
    tables = pd.read_html(url)
    return tables[0][column_name].tolist()

def save_tickers_to_file(tickers, filename):
    """Save tickers to a text file, one per line."""
    with open(filename, "w") as f:
        for ticker in tickers:
            f.write(ticker + "\n")

# Wikipedia URLs
sp500_url = "https://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
sp600_url = "https://en.wikipedia.org/wiki/List_of_S%26P_600_companies"

# Extract tickers
sp500_tickers = get_sp_tickers(sp500_url, "Symbol")
sp600_tickers = get_sp_tickers(sp600_url, "Symbol")

sp500_table = get_sp_table(sp500_url)
sp600_table = get_sp_table(sp600_url)


# Save to text files
save_tickers_to_file(sp500_tickers, "sp500_tickers.txt")
save_tickers_to_file(sp600_tickers, "sp600_tickers.txt")
sp500_table.to_csv('sp500_table.csv',index = False)
sp600_table.to_csv('sp600_table.csv',index = False)

**Cleaning**

In [266]:
sp500_m = pd.read_csv('SP500_Monthly.csv')
sp600_m = pd.read_csv("SP600_Monthly.csv")

# Clean
sp600_m = sp600_m[['public_date','TICKER','roa','roe','divyield']].copy()


# Clean
sp500_m = sp500_m[['public_date','TICKER','roa','roe','divyield']].copy()

# Tables
sp500_table = pd.read_csv('sp500_table.csv')
sp600_table = pd.read_csv('sp600_table.csv')

sp500_sector_map = sp500_table[['Symbol','GICS Sector']].rename(columns = {"Symbol":'TICKER','GICS Sector':"Sector"})
sp600_sector_map = sp600_table[['Symbol','GICS Sector']].rename(columns = {"Symbol":'TICKER','GICS Sector':"Sector"})

sp500_m = sp500_m.merge(sp500_sector_map,how = 'left',left_on = ['TICKER'],right_on = ['TICKER'])
sp600_m = sp600_m.merge(sp600_sector_map,how = 'left',left_on = ['TICKER'],right_on = ['TICKER'])

sp500_m.set_index('public_date',inplace=True)
sp500_m.index = pd.to_datetime(sp500_m.index).date

sp600_m.set_index('public_date',inplace=True)
sp600_m.index = pd.to_datetime(sp600_m.index).date

##### **Backtest**

In [277]:
(sp500_m.loc[sp500_m.index[0]]
 .groupby('Sector').apply(lambda x: x.nlargest(5, ['roa', 'roe',])))

/var/folders/__/wgnmk9j14kl1krf80l2c6bfw0000gn/T/ipykernel_32991/3390920543.py:2: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



TICKER    roa    roe divyield  \
Sector                                                            
Communication Services 2010-01-31   NFLX  0.345  0.321      NaN   
                       2010-01-31   GOOG  0.282  0.168      NaN   
                       2010-01-31     VZ  0.164  0.092    6.46%   
                       2010-01-31      T  0.151  0.096    6.62%   
                       2010-01-31  CMCSA  0.121  0.045    2.39%   
Consumer Discretionary 2010-01-31    DPZ  0.432    NaN      NaN   
                       2010-01-31   LULU  0.391  0.254      NaN   
                       2010-01-31   DECK  0.372  0.234      NaN   
                       2010-01-31   ROST  0.324  0.355    .958%   
                       2010-01-31    YUM  0.310  3.146    2.46%   
Consumer Staples       2010-01-31     CL  0.378  0.913    2.20%   
                       2010-01-31     PM  0.327  0.675    5.10%   
                       2010-01-31   DLTR  0.303  0.233      NaN   
                       2010-01-31    HSY  0.279  0.820    3.27%   
                       2010-01-31    CLX  0.279    NaN    3.38%   
Energy                 2010-01-31    HAL  0.240  0.214    1.23%   
                       2010-01-31    OXY  0.178  0.083    1.68%   
                       2010-01-31    EOG  0.176  0.051    .641%   
                       2010-01-31    XOM  0.173  0.157    2.61%   
                       2010-01-31    CVX  0.167  0.124    3.77%   
Financials             2010-01-31    FDS  0.425  0.308    1.27%   
                       2010-01-31    MCO  0.410    NaN    1.45%   
                       2010-01-31    WTW  0.393    NaN    2.43%   
                       2010-01-31     MA  0.354  0.635    .240%   
                       2010-01-31   JKHY  0.244  0.160    1.55%   
Health Care            2010-01-31   GILD  0.442  0.523      NaN   
                       2010-01-31   TECH  0.338  0.231    1.58%   
                       2010-01-31   IDXX  0.281  0.249      NaN   
                       2010-01-31    LLY  0.281 -0.023    5.57%   
                       2010-01-31   ISRG  0.255  0.168      NaN   
Industrials            2010-01-31   CHRW  0.337  0.328    1.77%   
                       2010-01-31    ROL  0.286  0.320    1.42%   
                       2010-01-31   FAST  0.278  0.174    1.78%   
                       2010-01-31   CPRT  0.267  0.159      NaN   
                       2010-01-31   JBHT  0.252  0.177    1.44%   
Information Technology 2010-01-31   FSLR  0.354  0.367      NaN   
                       2010-01-31   MSFT  0.314  0.381    1.85%   
                       2010-01-31   AAPL  0.285  0.296      NaN   
                       2010-01-31   CTSH  0.281  0.246      NaN   
                       2010-01-31    WDC  0.234  0.182      NaN   
Materials              2010-01-31     CF  0.597  0.323    .431%   
                       2010-01-31    ECL  0.216  0.203    1.41%   
                       2010-01-31    FMC  0.201  0.231    .982%   
                       2010-01-31    SHW  0.197  0.253    2.24%   
                       2010-01-31    PKG  0.189  0.253    2.72%   
Real Estate            2010-01-31   CSGP  0.158  0.073      NaN   
                       2010-01-31   EQIX  0.131  0.156      NaN   
                       2010-01-31    IRM  0.131  0.070      NaN   
                       2010-01-31    AMT  0.129  0.086      NaN   
                       2010-01-31   SBAC  0.097 -0.165      NaN   
Utilities              2010-01-31    EXC  0.148  0.167    4.60%   
                       2010-01-31    PEG  0.136  0.122    4.35%   
                       2010-01-31    NRG  0.131  0.151      NaN   
                       2010-01-31     FE  0.120  0.099    5.04%   
                       2010-01-31      D  0.117  0.116    4.67%   

                                                   Sector  
Sector                                                     
Communication Services 2010-01-31  Communication Services  
                       2010-01-31 

In [269]:
sp500_m.loc[sp500_m.index[0]]

TICKER    roa    roe divyield                  Sector
2010-01-31   ORCL  0.232  0.232    .867%  Information Technology
2010-01-31   MSFT  0.314  0.381    1.85%  Information Technology
2010-01-31   TROW  0.227  0.120    2.02%              Financials
2010-01-31    HON  0.133  0.240    3.13%             Industrials
2010-01-31    ADM  0.080  0.081    1.87%        Consumer Staples
...           ...    ...    ...      ...                     ...
2010-01-31    AWK  0.075 -0.049    3.85%               Utilities
2010-01-31    UNH  0.135  0.172    .091%             Health Care
2010-01-31    NaN  0.428    NaN      NaN                     NaN
2010-01-31    NaN  0.128  0.097      NaN                     NaN
2010-01-31    NaN  0.148    NaN      NaN                     NaN

[416 rows x 5 columns]

In [246]:
small_cap_tickers = sp600_m['TICKER'].unique()
small_cap_weights = pd.Series(0.0, index= small_cap_tickers, dtype=float)

large_cap_tickers = sp600_m['TICKER'].unique()
large_cap_weights = pd.Series(0.0, index= large_cap_tickers, dtype=float)

rebalance = 1
factors = ['roa','roe','divyield']
for i in range(min(len(sp600_m.index),len(sp500_m.index))):

    # Calcuate Returns
    # Need Daily Data

    if i % rebalance == 0:
        
        # large cap
        print(sp500_m.loc[sp500_m.index[i]].sort_values(factors))
        pass



           TICKER    roa    roe divyield
2010-01-31    COR -2.180 -3.008      NaN
2010-01-31   MRNA -0.886 -4.146      NaN
2010-01-31   DXCM -0.805 -6.880      NaN
2010-01-31   INCY -0.595    NaN      NaN
2010-01-31   PODD -0.525 -5.022      NaN
...           ...    ...    ...      ...
2010-01-31    DPZ  0.432    NaN      NaN
2010-01-31   GILD  0.442  0.523      NaN
2010-01-31    COH  0.478  0.404    .860%
2010-01-31     CF  0.597  0.323    .431%
2010-01-31     GS    NaN    NaN    .941%

[416 rows x 4 columns]
           TICKER    roa    roe divyield
2010-02-28   DXCM -0.952    NaN      NaN
2010-02-28   MRNA -0.773    NaN      NaN
2010-02-28   VRTX -0.385 -0.859      NaN
2010-02-28   PODD -0.384 -2.186      NaN
2010-02-28   MERR -0.303    NaN      NaN
...           ...    ...    ...      ...
2010-02-28   VRSK  0.448    NaN      NaN
2010-02-28    COH  0.458  0.389    .823%
2010-02-28    DPZ  0.461    NaN      NaN
2010-02-28     MS    NaN    NaN    .710%
2010-02-28     GS    NaN    NaN  

KeyboardInterrupt: 